In [32]:
import pandas as pd
import numpy as np
import requests
import warnings
import time
import re

from collections import Counter
from bs4 import BeautifulSoup
from datetime import datetime
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn import metrics

warnings.filterwarnings('ignore')

In [33]:
data = pd.read_csv('main_task.csv')

Описание столбцов
1. Restaurant_id — идентификационный номер ресторана;
2. City — город, в котором находится ресторан;
3. Cuisine Style — стиль или стили, к которым можно отнести блюда, предлагаемые в ресторане;
4. Ranking — место, которое занимает данный ресторан среди всех ресторанов своего города;
5. Rating — рейтинг ресторана по данным TripAdvisor (именно это значение должна будет предсказывать модель);
6. Price Range — диапазон цен в ресторане;
7. Number of Reviews — количество отзывов о ресторане;
8. Reviews — данные о двух отзывах, которые отображаются на сайте ресторана;
9. URL_TA — URL страницы ресторана на TripAdvosor;
10. ID_TA — идентификатор ресторана в базе данных TripAdvisor.

In [4]:
data.head(10)

Restaurant_id        City  \
0       id_5569       Paris   
1       id_1535   Stockholm   
2        id_352      London   
3       id_3456      Berlin   
4        id_615      Munich   
5       id_1418      Oporto   
6       id_1720       Milan   
7        id_825  Bratislava   
8       id_2690      Vienna   
9       id_4209        Rome   

                                       Cuisine Style  Ranking  Rating  \
0            ['European', 'French', 'International']   5570.0     3.5   
1                                                NaN   1537.0     4.0   
2  ['Japanese', 'Sushi', 'Asian', 'Grill', 'Veget...    353.0     4.5   
3                                                NaN   3458.0     5.0   
4  ['German', 'Central European', 'Vegetarian Fri...    621.0     4.0   
5                                                NaN   1419.0     3.0   
6                               ['Italian', 'Pizza']   1722.0     4.0   
7                                        ['Italian']    826.0     3.0   
8                                                NaN   2692.0     4.0   
9                  ['Italian', 'Pizza', 'Fast Food']   4210.0     4.0   

  Price Range  Number of Reviews  \
0    $$ - $$$              194.0   
1         NaN               10.0   
2        $$$$              688.0   
3         NaN                3.0   
4    $$ - $$$               84.0   
5         NaN                2.0   
6           $               50.0   
7         NaN                9.0   
8         NaN                NaN   
9           $               55.0   

                                             Reviews  \
0  [['Good food at your doorstep', 'A good hotel ...   
1  [['Unique cuisine', 'Delicious Nepalese food']...   
2  [['Catch up with friends', 'Not exceptional'],...   
3                                           [[], []]   
4  [['Best place to try a Bavarian food', 'Nice b...   
5  [['There are better 3 star hotel bars', 'Amazi...   
6  [['Excellent simple local eatery.', 'Excellent...   
7  [['Wasting of money', 'excellent cuisine'], ['...   
8                                           [[], []]   
9  [['Clean efficient staff', 'Nice little pizza ...   

                                              URL_TA      ID_TA  
0  /Restaurant_Review-g187147-d1912643-Reviews-R_...   d1912643  
1  /Restaurant_Review-g189852-d7992032-Reviews-Bu...   d7992032  
2  /Restaurant_Review-g186338-d8632781-Reviews-RO...   d8632781  
3  /Restaurant_Review-g187323-d1358776-Reviews-Es...   d1358776  
4  /Restaurant_Review-g187309-d6864963-Reviews-Au...   d6864963  
5  /Restaurant_Review-g189180-d12503536-Reviews-D...  d12503536  
6  /Restaurant_Review-g187849-d5808504-Reviews-Pi...   d5808504  
7  /Restaurant_Review-g274924-d3199765-Reviews-Ri...   d3199765  
8  /Restaurant_Review-g190454-d12845029-Reviews-G...  d12845029  
9  /Restaurant_Review-g187791-d8020681-Reviews-Qu...   d8020681

In [5]:
# посмотрим на заполнение стобцов
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 40000 entries, 0 to 39999
Data columns (total 10 columns):
Restaurant_id        40000 non-null object
City                 40000 non-null object
Cuisine Style        30717 non-null object
Ranking              40000 non-null float64
Rating               40000 non-null float64
Price Range          26114 non-null object
Number of Reviews    37457 non-null float64
Reviews              40000 non-null object
URL_TA               40000 non-null object
ID_TA                40000 non-null object
dtypes: float64(3), object(7)
memory usage: 3.1+ MB


9283 строки не содержат информацию о стиле/стилях кухни ресторанов (23,2% от количества объектов), 13886 строк не содержат информацию о диапазоне цен (34,7%), 2543 строки не содержат информации о количестве отзывов (6,3%)

In [12]:
reviews_without_number = data[data['Number of Reviews'].isnull()]
reviews_without_number.head(10)

Restaurant_id      City                        Cuisine Style  Ranking  \
8         id_2690    Vienna                                  NaN   2692.0   
21        id_5844    Madrid                                  NaN   5847.0   
32        id_1327  Budapest                                  NaN   1328.0   
102       id_1409  Budapest  ['French', 'European', 'Hungarian']   1410.0   
108       id_2047    Prague         ['Italian', 'Mediterranean']   2050.0   
167       id_8305     Paris                                  NaN   8306.0   
180       id_5023    Berlin                                  NaN   5025.0   
183       id_3566    Berlin                          ['Italian']   3568.0   
187       id_2847    Lisbon                                  NaN   2850.0   
199      id_16034    London                                  NaN  16046.0   

     Rating Price Range  Number of Reviews  \
8       4.0         NaN                NaN   
21      4.0         NaN                NaN   
32      5.0         NaN                NaN   
102     5.0         NaN                NaN   
108     5.0    $$ - $$$                NaN   
167     5.0         NaN                NaN   
180     4.0         NaN                NaN   
183     5.0         NaN                NaN   
187     4.0         NaN                NaN   
199     2.0         NaN                NaN   

                                               Reviews  \
8                                             [[], []]   
21                                            [[], []]   
32   [['Absolutely amazing, tasty, fresh, cheap Ch....   
102                                           [[], []]   
108                                           [[], []]   
167                                           [[], []]   
180  [['Free Wi-Fi, Peaceful, Pleasant'], ['01/19/2...   
183  [['Wonderful ambiance, delicious food, fantas....   
187  [['Affordable little cafe in the middle of Al....   
199                                           [[], []]   

                                                URL_TA      ID_TA  
8    /Restaurant_Review-g190454-d12845029-Reviews-G...  d12845029  
21   /Restaurant_Review-g187514-d10058810-Reviews-B...  d10058810  
32   /Restaurant_Review-g274887-d8791087-Reviews-Bu...   d8791087  
102  /Restaurant_Review-g274887-d13197631-Reviews-L...  d13197631  
108  /Restaurant_Review-g274707-d12243659-Reviews-T...  d12243659  
167  /Restaurant_Review-g187147-d13284434-Reviews-S...  d13284434  
180  /Restaurant_Review-g187323-d12068247-Reviews-K...  d12068247  
183  /Restaurant_Review-g187323-d2424319-Reviews-Fo...   d2424319  
187  /Restaurant_Review-g189158-d13139218-Reviews-C...  d13139218  
199  /Restaurant_Review-g186338-d7243246-Reviews-Yu...   d7243246

Оказывается, как видно, тексты отзывов есть не у всех ресторанов, но некоторые значения в столбце Reviews заполнены пустыми списками, что не равняется NaN. Можно будет заполнить отсутствующее значение в ячейке Number of Reviews для ресторанов, у которых есть список отзывов, взяв его длину. Для остальных заполнить значения нулями (как вариант, тут может измениться логика, пока не проходил дальше по заданиям)

Еще посмотрим на значения диапазона цен и рейтинга

In [27]:
print('Price range values = {}'.format(data['Price Range'].unique()))
print('Rating interval = {}'.format(data['Rating'].value_counts(bins=1).index[0]))
print('Rating values = {}'.format(data['Rating'].unique()))

Price range values = ['$$ - $$$' nan '$$$$' '$']
Rating interval = (0.995, 5.0]
Rating values = [ 3.5  4.   4.5  5.   3.   2.5  2.   1.   1.5]


##  Задание

<b>Из постановки задачи: мы должны использовать в модели датафрейм, содержащий только количественные признаки и не содержащий None-значений. На первом этапе для создания такого датафрейма давайте просто удалим столбцы, содержащие данные типа object, и заполним пропущенные значения (None или NaN) каким-то одним значением (нулём или средним арифметическим) для  всего столбца.<b>

Таким образом, удалим столбцы типа object, убедимся, что количество отзывов и место ресторана - целые значения и заполним нолями пропуски в столбце количества отзывов. Сохраним все в отдельную переменную task_df 

In [43]:
# проверим, что количество отзывов и места - целые числа
number_of_reviews = data['Number of Reviews'].dropna().apply(lambda x: x.is_integer())
ranking = data['Ranking'].dropna().apply(lambda x: x.is_integer())

print(number_of_reviews.unique(), ranking.unique())

[ True] [ True]


In [9]:
task_df = data.drop(labels=['Restaurant_id','City','Cuisine Style','Price Range','Reviews','URL_TA','ID_TA'], axis=1).fillna(0)

In [24]:
# Убедимся, что не осталось пропущенных значений
values = task_df.isnull().values
values[values == True].size

0

In [25]:
# Итоговый датафрейм
task_df.head()

Ranking  Rating  Number of Reviews
0   5570.0     3.5              194.0
1   1537.0     4.0               10.0
2    353.0     4.5              688.0
3   3458.0     5.0                3.0
4    621.0     4.0               84.0

Применим базовую модель из ноутбука you_first_model

In [37]:
X = task_df.iloc[:, [0, 2]]
y = task_df.iloc[:, 1]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25)

In [38]:
regr = RandomForestRegressor(n_estimators=100)
regr.fit(X_train, y_train)
y_pred = regr.predict(X_test)

print('MAE:', metrics.mean_absolute_error(y_test, y_pred))

MAE: 0.4316716077380952


Метрика MAE приняла значение 0.43. Учитывая, что рейтинг изменяется в интервале от 1 до 5 с шагом 0.5 (Rating values = [ 3.5  4.   4.5  5.   3.   2.5  2.   1.   1.5]), отклонение получилось довольно существенным. Очевидно, что нужно вводить больше признаков.

### Функции для обработки данных 

In [10]:
SITE = 'https://www.tripadvisor.com'

In [3]:
# Преобразование строкового представления списка в list (для признака "стили кухни")
def cuisines_to_list(string):
    return string.strip('[]').split(', ')

In [43]:
# Извлечение дат из значений признака Reviews
def get_dates(string):
    # [0-9|/]+
    pattern = re.compile('[0-9]{2}/[0-9]{2}/[0-9]{4}')
    dates = pattern.findall(string)
    
    if dates == []:
        return [np.nan] * 2
    elif len(dates) == 1:
        return dates + [np.nan]
    
    return dates

In [115]:
# Преобразование строкового представления списков в list (для признака Reviews)
def reviews_to_list(string, dates=False):
    pattern = re.compile('\'[^\']+\'')
    reviews = [word[1:-1] for word in pattern.findall(string)]
    
    if reviews == []:
        return [np.nan] * 2
    
    if dates:
        return reviews[-2:] if len(reviews) == 4 else [reviews[-1], np.nan]
    else:
        return reviews[:2] if len(reviews) == 4 else [reviews[0], np.nan]

In [63]:
def get_price_range_from_site(df):
    result = pd.Series()
    pattern = re.compile('\$\$ - \$\$\$|\$+')
    local_df = df.copy()
    filtered_df = local_df[local_df['Price Range'].isnull()]
    print('shape = {}'.format(filtered_df.shape[0]))
    indexes = filtered_df['Price Range'].index
    prs = []
    
    for i in range(filtered_df.shape[0]):
        time.sleep(2)
        try:
            response = requests.get(SITE + filtered_df.iloc[i]['URL_TA'])
        except Exception as err:
            print('Caught exception')
            print(err)
            prs = prs + [np.nan]
            #print('common = {}'.format(prs))
            continue
        
        page = BeautifulSoup(response.text, 'html.parser')
        string = page.find(class_='header_links')
        print('#{} url = {}\nstring = {}'.format(i + 1, filtered_df.iloc[i]['URL_TA'], string))
        
        if string is None:
            prs = prs + [np.nan]
            #print('common = {}'.format(prs))
            continue
        
        pr = pattern.findall(string.text)
        print('pr = {}\n'.format(pr))
        
        if pr != []:
            filtered_df.iloc[i]['Price Range'] = pr[0]
            prs = prs + pr
            #print('common = {}'.format(prs))
        else:
            prs = prs + [np.nan]
            #print('common = {}'.format(prs))
            continue
    
    return pd.Series(prs, index=indexes)

In [75]:
def get_additioinal_cuisines(df, all_cuisines):
    #pattern = re.compile('\$\$ - \$\$\$|\$+')
    local_df = df.copy()
    filtered_df = local_df[local_df['Cuisine Style'].isnull()]
    print('shape = {}'.format(filtered_df.shape[0]))
    indexes = filtered_df['Cuisine Style'].index
    cs = []
    
    for i in range(filtered_df.shape[0]):
        time.sleep(2)
        try:
            response = requests.get(SITE + filtered_df.iloc[i]['URL_TA'])
        except Exception as err:
            print('Caught exception')
            print(err)
            cs = cs + [np.nan]
            #print('common = {}'.format(cs))
            continue
            
        page = BeautifulSoup(response.text, 'html.parser')
        string = page.find(class_='header_links')
        print('#{} url = {}\nstring = {}'.format(i + 1, filtered_df.iloc[i]['URL_TA'], string))
        
        if string is None:
            cs = cs + [np.nan]
            #print('common = {}'.format(cs))
            continue
        
        temp = []
        for item in all_cuisines:
            if item in string.text:
                temp.append(item)
                
        print('temp = {}'.format(temp))
        if temp != []:
            #filtered_df.iloc[i]['Price Range'] = pr[0]
            cs.append(temp)
            #print('common = {}'.format(cs))
        else:
            cs = cs + [np.nan]
            #print('common = {}'.format(cs))
            continue
        
    return pd.Series(cs, index=indexes)

## Наполнение выборки данными 

In [12]:
# Сколько городов представлено в наборе данных?
data['City'].nunique()

31

In [8]:
data['City'].unique()

array(['Paris', 'Stockholm', 'London', 'Berlin', 'Munich', 'Oporto',
       'Milan', 'Bratislava', 'Vienna', 'Rome', 'Barcelona', 'Madrid',
       'Dublin', 'Brussels', 'Zurich', 'Warsaw', 'Budapest', 'Copenhagen',
       'Amsterdam', 'Lyon', 'Hamburg', 'Lisbon', 'Prague', 'Oslo',
       'Helsinki', 'Edinburgh', 'Geneva', 'Ljubljana', 'Athens',
       'Luxembourg', 'Krakow'], dtype=object)

In [11]:
# Сколько ресторанов расположены в столичных городах?
data.query('City not in ["Munich", "Oporto", "Milan", "Barcelona", "Zurich", "Lyon", "Hamburg", "Geneva", "Krakow"]').shape[0]

30424

In [72]:
# Сколько типов кухонь представлено в наборе данных?
all_cuisines = set()

for cuisine in data['Cuisine Style'].dropna():
    all_cuisines.update(cuisine.strip('[]').split(', '))

all_cuisines = set([cuisine[1:-1] for cuisine in all_cuisines])
len(all_cuisines)

125

In [33]:
# Какая кухня представлена в наибольшем количестве ресторанов? Введите название кухни без кавычек или апострофов.
c = Counter()

for cuisines in data['Cuisine Style'].dropna():
    for cuisine in cuisines.strip('[]').split(', '):
        c[cuisine.strip("\'")] += 1
        
print(c)

Counter({'Vegetarian Friendly': 11189, 'European': 10060, 'Mediterranean': 6277, 'Italian': 5964, 'Vegan Options': 4486, 'Gluten Free Options': 4113, 'Bar': 3297, 'French': 3190, 'Asian': 3011, 'Pizza': 2849, 'Spanish': 2798, 'Pub': 2449, 'Cafe': 2325, 'Fast Food': 1705, 'British': 1595, 'International': 1584, 'Seafood': 1505, 'Japanese': 1464, 'Central European': 1393, 'American': 1315, 'Sushi': 1156, 'Chinese': 1145, 'Portuguese': 1107, 'Indian': 1041, 'Middle Eastern': 782, 'Thai': 743, 'Wine Bar': 697, 'German': 662, 'Healthy': 620, 'Greek': 604, 'Halal': 598, 'Czech': 595, 'Fusion': 577, 'Steakhouse': 573, 'Barbecue': 555, 'Contemporary': 523, 'Vietnamese': 513, 'Eastern European': 496, 'Soups': 494, 'Grill': 490, 'Gastropub': 471, 'Mexican': 445, 'Turkish': 444, 'Delicatessen': 392, 'Austrian': 380, 'South American': 372, 'Polish': 365, 'Hungarian': 352, 'Scandinavian': 342, 'Lebanese': 329, 'Latin': 302, 'Diner': 295, 'Dutch': 294, 'Irish': 284, 'Belgian': 270, 'Street Food': 26

In [43]:
# Какое среднее количество кухонь предлагается в одном ресторане?
# Если в данных отсутствует информация о типах кухонь, то считайте, что в этом ресторане предлагается только один тип кухни. 
# Ответ округлите до одного знака после запятой.

cuisines = data.loc[:, 'Cuisine Style'].fillna('[Vegetarian Friendly]')
cuisines = cuisines.apply(lambda x: cuisines_to_list(x))

cuisines_in_all_restaurants = []

for cuisine in cuisines:
    cuisines_in_all_restaurants.append(len(cuisine))

print(np.mean(cuisines_in_all_restaurants))

2.6224


In [34]:
reviews = data.loc[:, 'Reviews']
reviews_dates = reviews.apply(lambda x: get_dates(x))

dates_df = pd.concat([pd.Series([date[0] for date in reviews_dates]),
                      pd.Series([date[1] for date in reviews_dates])], axis=1)

dates_df.columns = ['FRDate', 'SRDate']
dates_df['FRDate'] = pd.to_datetime(dates_df['FRDate'])
dates_df['SRDate'] = pd.to_datetime(dates_df['SRDate'])

dates_df.head()

FRDate     SRDate
0 2017-12-31 2017-11-20
1 2017-07-06 2016-06-19
2 2018-01-08 2018-01-06
3        NaT        NaT
4 2017-11-18 2017-02-19

In [40]:
dates_df['Days Delta'] = dates_df['FRDate'] - dates_df['SRDate']
dates_df[dates_df['Days Delta'] == dates_df['Days Delta'].max()]

FRDate     SRDate Days Delta
7990 2016-10-02 2007-12-22  3207 days

In [42]:
# Когда был оставлен самый свежий отзыв?
print(dates_df['FRDate'].max(), dates_df['SRDate'].max())

2018-02-26 00:00:00 2018-02-26 00:00:00


In [63]:
reviews_to_list("[['Fresh, hot, wonderful dumplings!'], ['03/19/2017']]", False)

['Fresh', 'hot']

In [84]:
"[['Fresh, hot, wonderful dumplings!'], ['03/19/2017']]"[1:-1]#.replace('[', '').replace(']', '').split('\', \'')

"['Fresh, hot, wonderful dumplings!'], ['03/19/2017']"

In [18]:
#(\'\d\d\/\d\d\/\d\d\d\d\')
#(\'[^\']+\')|(\"\".*\"\")
#(\'[^\']+\')|(""(?:[^"\\]++|\\.)*+"")|(\"\".*\"\")
pattern = re.compile('[0-9]{2}/[0-9]{2}/[0-9]{4}')

In [19]:
pattern.findall("[['Great selection of Portugese cuisine. Grea...', 'New year 2017/18'], ['01/03/2018', '12/31/2017']]")

['01/03/2018', '12/31/2017']

Итак, наполним основной датафрейм данными. Для начала признак Price Range переведем в текстовое представление по ценовому диапазону. Заменим значения в столбце, а диапазон зададим значениями low, middle, high. Перед этим попробуем сделать запрос на сайт TripAdvisor и для ресторанов, у которых нет ценового диапазона, получить его

In [6]:
data.iloc[1].URL_TA

'/Restaurant_Review-g189852-d7992032-Reviews-Buddha_Nepal-Stockholm.html'

In [15]:
url = 'https://www.tripadvisor.com'
response = requests.get('https://www.tripadvisor.com/Restaurant_Review-g188590-d8396543-Reviews-Maes-Amsterdam_North_Holland_Province.html')

page = BeautifulSoup(response.text, 'html.parser')
string = page.find(class_='header_links')


In [16]:
print(string)

None


In [91]:
pattern = re.compile('\$\$ - \$\$\$|\$+')
pattern.findall(string.text)

['$$ - $$$']

In [64]:
%timeit
t_df = data.copy()
pr = get_price_range_from_site(t_df)

shape = 13886
#1 url = /Restaurant_Review-g189852-d7992032-Reviews-Buddha_Nepal-Stockholm.html
string = <div class="header_links"><a href="/Restaurants-g189852-Stockholm.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g189852-c3-Stockholm.html">Asian</a>, Nepali</div>
pr = ['$$ - $$$']

#2 url = /Restaurant_Review-g187323-d1358776-Reviews-Esplanade-Berlin.html
string = None
#3 url = /Restaurant_Review-g189180-d12503536-Reviews-Dick_s_Bar-Porto_Porto_District_Northern_Portugal.html
string = <div class="header_links"><a href="/Restaurants-g189180-Porto_Porto_District_Northern_Portugal.html?pid=6">$$ - $$$</a>, Bar, <a href="/Restaurants-g189180-c18-Porto_Porto_District_Northern_Portugal.html">European</a>, <a href="/Restaurants-g189180-c10680-Porto_Porto_District_Northern_Portugal.html">Portuguese</a></div>
pr = ['$$ - $$$']

#4 url = /Restaurant_Review-g274924-d3199765-Reviews-Ristorante_Italiano_San_Cono-Bratislava_Bratislava_Region.html
string = <div class="header_links"><a href="/Res

#33 url = /Restaurant_Review-g1136488-d5599563-Reviews-Le_Chalet_de_la_Foret-Uccle_Brussels.html
string = <div class="header_links"><a href="/Restaurants-g1136488-Uccle_Brussels.html?pid=8">$$$$</a>, <a href="/Restaurants-g1136488-c20-Uccle_Brussels.html">French</a>, <a href="/Restaurants-g1136488-c18-Uccle_Brussels.html">European</a></div>
pr = ['$$$$']

#34 url = /Restaurant_Review-g187265-d7623654-Reviews-Creperie_Caramel_Sale-Lyon_Rhone_Auvergne_Rhone_Alpes.html
string = <div class="header_links"><a href="/Restaurants-g187265-Lyon_Rhone_Auvergne_Rhone_Alpes.html?pid=1">$</a>, <a href="/Restaurants-g187265-c20-Lyon_Rhone_Auvergne_Rhone_Alpes.html">French</a>, <a href="/Restaurants-g187265-zfz10665-Lyon_Rhone_Auvergne_Rhone_Alpes.html">Vegetarian Friendly</a></div>
pr = ['$']

#35 url = /Restaurant_Review-g274707-d4768085-Reviews-McDonald_s_Florenc-Prague_Bohemia.html
string = <div class="header_links"><a href="/Restaurants-g274707-Prague_Bohemia.html?pid=1">$</a>, <a href="/Restaura

#65 url = /Restaurant_Review-g187323-d2424319-Reviews-Focolare-Berlin.html
string = <div class="header_links"><a href="/Restaurants-g187323-c26-Berlin.html">Italian</a></div>
pr = []

#66 url = /Restaurant_Review-g186338-d10677156-Reviews-Bombay_Spice-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=1">$</a>, <a href="/Restaurants-g186338-c24-London_England.html">Indian</a>, <a href="/Restaurants-g186338-c3-London_England.html">Asian</a>, <a href="/Restaurants-g186338-zfz10665-London_England.html">Vegetarian Friendly</a></div>
pr = ['$']

#67 url = /Restaurant_Review-g187514-d9562461-Reviews-Ottawa_Burger-Madrid.html
string = <div class="header_links"><a href="/Restaurants-g187514-Madrid.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187514-c2-Madrid.html">American</a>, <a href="/Restaurants-g187514-c10646-Madrid.html">Fast Food</a></div>
pr = ['$$ - $$$']

#68 url = /Restaurant_Review-g189158-d5979704-Reviews-Pastelaria_Ana

#96 url = /Restaurant_Review-g187514-d5795989-Reviews-Asturias-Madrid.html
string = None
#97 url = /Restaurant_Review-g187849-d8339930-Reviews-City-Milan_Lombardy.html
string = None
#98 url = /Restaurant_Review-g187849-d6278406-Reviews-Bicos_Cafe-Milan_Lombardy.html
string = None
#99 url = /Restaurant_Review-g187497-d10039662-Reviews-La_Cova_D_horta-Barcelona_Catalonia.html
string = <div class="header_links"><a href="/Restaurants-g187497-Barcelona_Catalonia.html?pid=1">$</a>, <a href="/Restaurants-g187497-c36-Barcelona_Catalonia.html">Spanish</a>, <a href="/Restaurants-g187497-zfz10665-Barcelona_Catalonia.html">Vegetarian Friendly</a></div>
pr = ['$']

#100 url = /Restaurant_Review-g187147-d1035596-Reviews-L_Envol_Cafe_Quebecois-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=6">$$ - $$$</a></div>
pr = ['$$ - $$$']

#101 url = /Restaurant_Review-g186338-d12512228-Reviews-The_BBQ_Club-London_England.html
string = <di

#133 url = /Restaurant_Review-g187147-d12321528-Reviews-French_Home-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187147-c2-Paris_Ile_de_France.html">American</a>, <a href="/Restaurants-g187147-c20-Paris_Ile_de_France.html">French</a>, <a href="/Restaurants-g187147-zfz10665-Paris_Ile_de_France.html">Vegetarian Friendly</a></div>
pr = ['$$ - $$$']

#134 url = /Restaurant_Review-g187849-d8339764-Reviews-Bar_Gold-Milan_Lombardy.html
string = <div class="header_links"><a href="/Restaurants-g187849-Milan_Lombardy.html?pid=1">$</a></div>
pr = ['$']

#135 url = /Restaurant_Review-g186338-d5442851-Reviews-Queen_s_Crescent_Grill-London_England.html
string = None
#136 url = /Restaurant_Review-g190454-d7097810-Reviews-Eiscafe_Renzo-Vienna.html
string = None
#137 url = /Restaurant_Review-g188057-d7996902-Reviews-Lidia-Geneva.html
string = None
#138 url = /Restaurant_Review-g187323-d1354

...

#13722 url = /Restaurant_Review-g186338-d5443388-Reviews-Marina_Fish_Bar-London_England.html
string = None
#13723 url = /Restaurant_Review-g187323-d1341784-Reviews-Restaurant_im_Ethnologischen_Museum-Berlin.html
string = None
#13724 url = /Restaurant_Review-g189400-d695901-Reviews-Frame-Athens_Attica.html
string = None
#13725 url = /Restaurant_Review-g188590-d6440857-Reviews-El_Amor-Amsterdam_North_Holland_Province.html
string = <div class="header_links"><a href="/Restaurants-g188590-c36-Amsterdam_North_Holland_Province.html">Spanish</a></div>
pr = []

#13726 url = /Restaurant_Review-g188057-d11734083-Reviews-Le_Bistrot-Geneva.html
string = <div class="header_links"><a href="/Restaurants-g188057-Geneva.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g188057-c8-Geneva.html">Cafe</a></div>
pr = ['$$ - $$$']

#13727 url = /Restaurant_Review-g187497-d697434-Reviews-Bunga_Raya-Barcelona_Catalonia.html
string = <div class="header_links"><a href="/Restaurants-g187497-c3-Barcelona_Catalonia.ht

#13756 url = /Restaurant_Review-g187331-d13331672-Reviews-Restaurant_Luisenhof_Dubrovnik-Hamburg.html
string = <div class="header_links"><a href="/Restaurants-g187331-Hamburg.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187331-c21-Hamburg.html">German</a>, Croatian, <a href="/Restaurants-g187331-c18-Hamburg.html">European</a></div>
pr = ['$$ - $$$']

#13757 url = /Restaurant_Review-g274873-d11924327-Reviews-Krakovc-Ljubljana_Upper_Carniola_Region.html
string = <div class="header_links"><a href="/Restaurants-g274873-Ljubljana_Upper_Carniola_Region.html?pid=1">$</a>, <a href="/Restaurants-g274873-c8-Ljubljana_Upper_Carniola_Region.html">Cafe</a>, Bar, <a href="/Restaurants-g274873-c6-Ljubljana_Upper_Carniola_Region.html">Barbecue</a></div>
pr = ['$']

#13758 url = /Restaurant_Review-g187514-d6705984-Reviews-Amor_al_Plato_Restaurant-Madrid.html
string = <div class="header_links"><a href="/Restaurants-g187514-Madrid.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187514-c36-Madrid.htm

#13789 url = /Restaurant_Review-g190454-d10792080-Reviews-Gutenbergs_Kantine-Vienna.html
string = <div class="header_links"><a href="/Restaurants-g190454-Vienna.html?pid=6">$$ - $$$</a></div>
pr = ['$$ - $$$']

#13790 url = /Restaurant_Review-g187497-d4833406-Reviews-Bienvenidos-Barcelona_Catalonia.html
string = <div class="header_links"><a href="/Restaurants-g187497-c26-Barcelona_Catalonia.html">Italian</a>, <a href="/Restaurants-g187497-c28-Barcelona_Catalonia.html">Mediterranean</a>, <a href="/Restaurants-g187497-c36-Barcelona_Catalonia.html">Spanish</a></div>
pr = []

#13791 url = /Restaurant_Review-g187497-d13201110-Reviews-Llarmuk-Barcelona_Catalonia.html
string = None
#13792 url = /Restaurant_Review-g187497-d12207476-Reviews-Bar_Social_del_Centre-Barcelona_Catalonia.html
string = <div class="header_links"><a href="/Restaurants-g187497-Barcelona_Catalonia.html?pid=1">$</a></div>
pr = ['$']

#13793 url = /Restaurant_Review-g187147-d1322585-Reviews-Tribal_Cafe-Paris_Ile_de_France.h

#13825 url = /Restaurant_Review-g187147-d8398659-Reviews-Cathay_House-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187147-c11-Paris_Ile_de_France.html">Chinese</a>, <a href="/Restaurants-g187147-c27-Paris_Ile_de_France.html">Japanese</a>, <a href="/Restaurants-g187147-c3-Paris_Ile_de_France.html">Asian</a></div>
pr = ['$$ - $$$']

#13826 url = /Restaurant_Review-g188057-d1045091-Reviews-Yamakawa-Geneva.html
string = <div class="header_links"><a href="/Restaurants-g188057-c27-Geneva.html">Japanese</a>, <a href="/Restaurants-g188057-c3-Geneva.html">Asian</a></div>
pr = []

#13827 url = /Restaurant_Review-g187147-d1035294-Reviews-Le_Marcande-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-c20-Paris_Ile_de_France.html">French</a></div>
pr = []

#13828 url = /Restaurant_Review-g187323-d10822286-Reviews-Lindner_Hotel_Am_Ku_Damm-Berlin.htm

#13854 url = /Restaurant_Review-g1136493-d10524953-Reviews-Malewa-Ixelles_Brussels.html
string = None
#13855 url = /Restaurant_Review-g187497-d6756273-Reviews-Marina_Vins_i_Vermut-Barcelona_Catalonia.html
string = None
#13856 url = /Restaurant_Review-g187514-d4100696-Reviews-McDonald_s-Madrid.html
string = <div class="header_links"><a href="/Restaurants-g187514-Madrid.html?pid=1">$</a>, <a href="/Restaurants-g187514-c10646-Madrid.html">Fast Food</a></div>
pr = ['$']

#13857 url = /Restaurant_Review-g274856-d6523244-Reviews-22_Nowy_Swiat_Bistro_Burger-Warsaw_Mazovia_Province_Central_Poland.html
string = <div class="header_links"><a href="/Restaurants-g274856-c2-Warsaw_Mazovia_Province_Central_Poland.html">American</a>, <a href="/Restaurants-g274856-c10637-Warsaw_Mazovia_Province_Central_Poland.html">Polish</a>, <a href="/Restaurants-g274856-c18-Warsaw_Mazovia_Province_Central_Poland.html">European</a></div>
pr = []

#13858 url = /Restaurant_Review-g187791-d7106787-Reviews-Peperino_pizze

In [76]:
cs = get_additioinal_cuisines(t_df, all_cuisines)

shape = 9283
#1 url = /Restaurant_Review-g189852-d7992032-Reviews-Buddha_Nepal-Stockholm.html
string = <div class="header_links"><a href="/Restaurants-g189852-Stockholm.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g189852-c3-Stockholm.html">Asian</a>, Nepali</div>
temp = ['Asian', 'Nepali']
#2 url = /Restaurant_Review-g187323-d1358776-Reviews-Esplanade-Berlin.html
string = None
#3 url = /Restaurant_Review-g189180-d12503536-Reviews-Dick_s_Bar-Porto_Porto_District_Northern_Portugal.html
string = <div class="header_links"><a href="/Restaurants-g189180-Porto_Porto_District_Northern_Portugal.html?pid=6">$$ - $$$</a>, Bar, <a href="/Restaurants-g189180-c18-Porto_Porto_District_Northern_Portugal.html">European</a>, <a href="/Restaurants-g189180-c10680-Porto_Porto_District_Northern_Portugal.html">Portuguese</a></div>
temp = ['European', 'Bar', 'Portuguese']
#4 url = /Restaurant_Review-g190454-d12845029-Reviews-Grunstern-Vienna.html
string = <div class="header_links"><a href="/Restaurants-g1

#34 url = /Restaurant_Review-g187147-d13094972-Reviews-Love_Juice_Bar-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-zfz10665-Paris_Ile_de_France.html">Vegetarian Friendly</a></div>
temp = ['Vegetarian Friendly']
#35 url = /Restaurant_Review-g186338-d7994738-Reviews-Slim_Jim_s_Liquor_Store-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=1">$</a></div>
temp = []
#36 url = /Restaurant_Review-g187147-d3612769-Reviews-Bubbolitas-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=1">$</a></div>
temp = []
#37 url = /Restaurant_Review-g187497-d5867903-Reviews-Fer_El_Cafe-Barcelona_Catalonia.html
string = None
#38 url = /Restaurant_Review-g274924-d12111665-Reviews-Vespa_Caffeterria-Bratislava_Bratislava_Region.html
string = <div class="header_links"><a href="/Restaurants-g274924-Bratislava_Bratislava_Region.html?pid=1">$</a>

#66 url = /Restaurant_Review-g187849-d8339930-Reviews-City-Milan_Lombardy.html
string = None
#67 url = /Restaurant_Review-g187849-d6278406-Reviews-Bicos_Cafe-Milan_Lombardy.html
string = None
#68 url = /Restaurant_Review-g187497-d10039662-Reviews-La_Cova_D_horta-Barcelona_Catalonia.html
string = <div class="header_links"><a href="/Restaurants-g187497-Barcelona_Catalonia.html?pid=1">$</a>, <a href="/Restaurants-g187497-c36-Barcelona_Catalonia.html">Spanish</a>, <a href="/Restaurants-g187497-zfz10665-Barcelona_Catalonia.html">Vegetarian Friendly</a></div>
temp = ['Spanish', 'Vegetarian Friendly']
#69 url = /Restaurant_Review-g187147-d1035596-Reviews-L_Envol_Cafe_Quebecois-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=6">$$ - $$$</a></div>
temp = []
#70 url = /Restaurant_Review-g186338-d12512228-Reviews-The_BBQ_Club-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.ht

#103 url = /Restaurant_Review-g188644-d10814311-Reviews-Ty_Penty-Brussels.html
string = None
#104 url = /Restaurant_Review-g186338-d1097059-Reviews-Asta_3-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=1">$</a></div>
temp = []
#105 url = /Restaurant_Review-g1136493-d12428801-Reviews-Chez_Charly-Ixelles_Brussels.html
string = None
#106 url = /Restaurant_Review-g187323-d1360884-Reviews-Annchen_von_Tharau-Berlin.html
string = <div class="header_links"><a href="/Restaurants-g187323-c21-Berlin.html">German</a></div>
temp = ['German']
#107 url = /Restaurant_Review-g187147-d12229735-Reviews-Boulangerie_Benoit_Benoit-Paris_Ile_de_France.html
string = None
#108 url = /Restaurant_Review-g187147-d5787627-Reviews-Ankka_Madeleine-Paris_Ile_de_France.html
string = None
#109 url = /Restaurant_Review-g189180-d7992689-Reviews-Abel_Sernadas-Porto_Porto_District_Northern_Portugal.html
string = None
#110 url = /Restaurant_Review-g186338-d104380

#141 url = /Restaurant_Review-g189180-d7644937-Reviews-NekaNau_Restaurante-Porto_Porto_District_Northern_Portugal.html
string = <div class="header_links">Bar, Pub</div>
temp = ['Bar', 'Pub']
#142 url = /Restaurant_Review-g187514-d10028124-Reviews-La_Bodega_De_Casanova-Madrid.html
string = <div class="header_links"><a href="/Restaurants-g187514-Madrid.html?pid=1">$</a></div>
temp = []
#143 url = /Restaurant_Review-g187514-d10784649-Reviews-Restaurante_Crono_Cristalia-Madrid.html
string = <div class="header_links"><a href="/Restaurants-g187514-Madrid.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187514-c28-Madrid.html">Mediterranean</a>, <a href="/Restaurants-g187514-c36-Madrid.html">Spanish</a></div>
temp = ['Spanish', 'Mediterranean']
#144 url = /Restaurant_Review-g187147-d10040334-Reviews-Comics_Burger-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187147-c2-Paris_Ile_de_

...

#9131 url = /Restaurant_Review-g186338-d3373686-Reviews-86-London_England.html
string = None
#9132 url = /Restaurant_Review-g187849-d13198211-Reviews-Top_Pan-Milan_Lombardy.html
string = <div class="header_links"><a href="/Restaurants-g187849-Milan_Lombardy.html?pid=1">$</a>, <a href="/Restaurants-g187849-c11-Milan_Lombardy.html">Chinese</a>, <a href="/Restaurants-g187849-c27-Milan_Lombardy.html">Japanese</a>, <a href="/Restaurants-g187849-c38-Milan_Lombardy.html">Sushi</a></div>
temp = ['Japanese', 'Chinese', 'Sushi']
#9133 url = /Restaurant_Review-g187147-d8520168-Reviews-Les_Fournils_De_Paris-Paris_Ile_de_France.html
string = <div class="header_links"><a href="/Restaurants-g187147-Paris_Ile_de_France.html?pid=1">$</a></div>
temp = []
#9134 url = /Restaurant_Review-g186605-d4128410-Reviews-CafeByDay-Dublin_County_Dublin.html
string = <div class="header_links"><a href="/Restaurants-g186605-c8-Dublin_County_Dublin.html">Cafe</a></div>
temp = ['Cafe']
#9135 url = /Restaurant_Review-g207

#9165 url = /Restaurant_Review-g186338-d11858253-Reviews-Stables_Cafe_Osterly_Park-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g186338-c8-London_England.html">Cafe</a>, <a href="/Restaurants-g186338-c7-London_England.html">British</a>, <a href="/Restaurants-g186338-zfz10665-London_England.html">Vegetarian Friendly</a></div>
temp = ['British', 'Cafe', 'Vegetarian Friendly']
#9166 url = /Restaurant_Review-g274707-d7124306-Reviews-Ovocny_Svetozor-Prague_Bohemia.html
string = <div class="header_links"><a href="/Restaurants-g274707-Prague_Bohemia.html?pid=1">$</a></div>
temp = []
#9167 url = /Restaurant_Review-g188644-d7205432-Reviews-Le_Cap_d_Argent-Brussels.html
string = None
#9168 url = /Restaurant_Review-g274887-d7594520-Reviews-Telefon_bistro-Budapest_Central_Hungary.html
string = None
#9169 url = /Restaurant_Review-g187147-d1066515-Reviews-Les_valseuses-Paris_Ile_de_France.html
stri

#9198 url = /Restaurant_Review-g190454-d1024338-Reviews-Hold-Vienna.html
string = <div class="header_links"><a href="/Restaurants-g190454-Vienna.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g190454-c26-Vienna.html">Italian</a>, <a href="/Restaurants-g190454-c18-Vienna.html">European</a></div>
temp = ['European', 'Italian']
#9199 url = /Restaurant_Review-g187323-d1340887-Reviews-Caravela-Berlin.html
string = <div class="header_links"><a href="/Restaurants-g187323-Berlin.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187323-c18-Berlin.html">European</a>, <a href="/Restaurants-g187323-c10680-Berlin.html">Portuguese</a></div>
temp = ['European', 'Portuguese']
#9200 url = /Restaurant_Review-g186338-d12308533-Reviews-EAT_Eastcheap-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=1">$</a>, <a href="/Restaurants-g186338-c10646-London_England.html">Fast Food</a></div>
temp = ['Fast Food']
#9201 url = /Restaurant_Review-g207356-d66

#9235 url = /Restaurant_Review-g190454-d5976508-Reviews-Yildiz_Kebap_Pizza_Schnitzelhaus-Vienna.html
string = None
#9236 url = /Restaurant_Review-g189400-d8710080-Reviews-Victoria-Athens_Attica.html
string = None
#9237 url = /Restaurant_Review-g187497-d1081683-Reviews-Mo_ma-Barcelona_Catalonia.html
string = None
#9238 url = /Restaurant_Review-g274856-d10802051-Reviews-Restauracja_Magat-Warsaw_Mazovia_Province_Central_Poland.html
string = None
#9239 url = /Restaurant_Review-g187514-d5489152-Reviews-Que_Comes-Madrid.html
string = None
#9240 url = /Restaurant_Review-g187323-d10822286-Reviews-Lindner_Hotel_Am_Ku_Damm-Berlin.html
string = None
#9241 url = /Restaurant_Review-g274772-d10810513-Reviews-Rest_Krak_Gastrox-Krakow_Lesser_Poland_Province_Southern_Poland.html
string = <div class="header_links"><a href="/Restaurants-g274772-Krakow_Lesser_Poland_Province_Southern_Poland.html?pid=1">$</a>, <a href="/Restaurants-g274772-c10637-Krakow_Lesser_Poland_Province_Southern_Poland.html">Polish</

#9270 url = /Restaurant_Review-g186338-d5079290-Reviews-The_Roman_Empire-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=6">$$ - $$$</a></div>
temp = []
#9271 url = /Restaurant_Review-g187514-d5609006-Reviews-La_Cuchara_Restaurante_Asador-Madrid.html
string = <div class="header_links"><a href="/Restaurants-g187514-Madrid.html?pid=6">$$ - $$$</a>, <a href="/Restaurants-g187514-c36-Madrid.html">Spanish</a></div>
temp = ['Spanish']
#9272 url = /Restaurant_Review-g186338-d12458176-Reviews-Cafe_Broadway-London_England.html
string = <div class="header_links"><a href="/Restaurants-g186338-London_England.html?pid=1">$</a></div>
temp = []
#9273 url = /Restaurant_Review-g187497-d12977288-Reviews-Greta_Brunch_Vermut-Barcelona_Catalonia.html
string = <div class="header_links">Diner, <a href="/Restaurants-g187497-c36-Barcelona_Catalonia.html">Spanish</a>, <a href="/Restaurants-g187497-c8-Barcelona_Catalonia.html">Cafe</a></div>
temp = ['S

In [73]:
all_cuisines

{'Afghani',
 'African',
 'Albanian',
 'American',
 'Arabic',
 'Argentinean',
 'Armenian',
 'Asian',
 'Australian',
 'Austrian',
 'Azerbaijani',
 'Balti',
 'Bangladeshi',
 'Bar',
 'Barbecue',
 'Belgian',
 'Brazilian',
 'Brew Pub',
 'British',
 'Burmese',
 'Cafe',
 'Cajun & Creole',
 'Cambodian',
 'Canadian',
 'Caribbean',
 'Caucasian',
 'Central American',
 'Central Asian',
 'Central European',
 'Chilean',
 'Chinese',
 'Colombian',
 'Contemporary',
 'Croatian',
 'Cuban',
 'Czech',
 'Danish',
 'Delicatessen',
 'Diner',
 'Dutch',
 'Eastern European',
 'Ecuadorean',
 'Egyptian',
 'Ethiopian',
 'European',
 'Fast Food',
 'Filipino',
 'French',
 'Fujian',
 'Fusion',
 'Gastropub',
 'Georgian',
 'German',
 'Gluten Free Options',
 'Greek',
 'Grill',
 'Halal',
 'Hawaiian',
 'Healthy',
 'Hungarian',
 'Indian',
 'Indonesian',
 'International',
 'Irish',
 'Israeli',
 'Italian',
 'Jamaican',
 'Japanese',
 'Korean',
 'Kosher',
 'Latin',
 'Latvian',
 'Lebanese',
 'Malaysian',
 'Mediterranean',
 'Mexic

In [9]:
t_df[t_df.URL_TA == '/Restaurant_Review-g188590-d8396543-Reviews-Maes-Amsterdam_North_Holland_Province.html']

Restaurant_id       City Cuisine Style  Ranking  Rating Price Range  \
30548       id_2654  Amsterdam           NaN   2661.0     3.5         NaN   

       Number of Reviews                                            Reviews  \
30548                3.0  [['Just about the perfect B&B', "Mae's B&B sti...   

                                                  URL_TA     ID_TA  
30548  /Restaurant_Review-g188590-d8396543-Reviews-Ma...  d8396543

In [21]:
t_df.iloc[30551]['URL_TA']

'/Restaurant_Review-g187514-d5971950-Reviews-Restaurante_O_Camino-Madrid.html'

In [67]:
t_df[t_df['Cuisine Style'].isnull()]


Restaurant_id       City Cuisine Style  Ranking  Rating Price Range  \
1           id_1535  Stockholm           NaN   1537.0     4.0         NaN   
3           id_3456     Berlin           NaN   3458.0     5.0         NaN   
5           id_1418     Oporto           NaN   1419.0     3.0         NaN   
8           id_2690     Vienna           NaN   2692.0     4.0         NaN   
10          id_6578  Barcelona           NaN   6579.0     3.0         NaN   
...             ...        ...           ...      ...     ...         ...   
39981        id_924       Lyon           NaN    925.0     4.0         NaN   
39983       id_2487  Amsterdam           NaN   2494.0     4.5         NaN   
39986       id_7274     Madrid           NaN   7279.0     3.0         NaN   
39988       id_4968     Berlin           NaN   4970.0     4.0         NaN   
39993       id_6057      Paris           NaN   6058.0     4.0         NaN   

       Number of Reviews                                            Reviews  \
1                   10.0  [['Unique cuisine', 'Delicious Nepalese food']...   
3                    3.0                                           [[], []]   
5                    2.0  [['There are better 3 star hotel bars', 'Amazi...   
8                    NaN                                           [[], []]   
10                   6.0                                           [[], []]   
...                  ...                                                ...   
39981               29.0                                           [[], []]   
39983                2.0   [['Italian food, as in Italy!'], ['05/24/2015']]   
39986                NaN                                           [[], []]   
39988                NaN                                           [[], []]   
39993               16.0  [['Naught but VERY nice', 'Yum'], ['01/23/2017...   

                                                  URL_TA      ID_TA  
1      /Restaurant_Review-g189852-d7992032-Reviews-Bu...   d7992032  
3      /Restaurant_Review-g187323-d1358776-Reviews-Es...   d1358776  
5      /Restaurant_Review-g189180-d12503536-Reviews-D...  d12503536  
8      /Restaurant_Review-g190454-d12845029-Reviews-G...  d12845029  
10     /Restaurant_Review-g187497-d10696479-Reviews-R...  d10696479  
...                                                  ...        ...  
39981  /Restaurant_Review-g187265-d5850306-Reviews-Re...   d5850306  
39983  /Restaurant_Review-g188590-d8120959-Reviews-Sa...   d8120959  
39986  /Restaurant_Review-g187514-d12182212-Reviews-C...  d12182212  
39988  /Restaurant_Review-g187323-d7761701-Reviews-Ar...   d7761701  
39993  /Restaurant_Review-g187147-d10532509-Reviews-B...  d10532509  

[9283 rows x 10 columns]

In [38]:
temp = t_df[t_df['Price Range'].isnull()]

In [65]:
pr

1        $$ - $$$
3             NaN
5        $$ - $$$
7             NaN
8             NaN
           ...   
39988         NaN
39989         NaN
39990         NaN
39993    $$ - $$$
39997         NaN
Length: 13886, dtype: object

In [66]:
pr.to_csv('additional_price_ranges.csv')

In [78]:
cs.to_csv('additional_cuisines.csv')